# Optimize Initial Conditions
## Yabox

In [1]:
from scipy.optimize import brute
import numpy as np
from datetime import datetime,timedelta
import pandas as pd
from yabox import DE

# Initialize Ray

In [2]:
from environs import Env
env = Env()
env.str("CUDA_DEVICE_ORDER",'PCI_BUS_ID')
env.int("CUDA_VISIBLE_DEVICES",1)
env.int("NUMBA_ENABLE_CUDASIM",1)
env.bool("OMPI_MCA_opal_cuda_support",True)

import os
import ray
MB=1024*1024
GB=MB*1024
ray.shutdown()
ray.init(object_store_memory=1*GB,memory=1*GB,
         #lru_evict=True,
         driver_object_store_memory=500*MB,num_gpus=4,num_cpus=10,
         ignore_reinit_error=True) # , include_webui=False, ignore_reinit_error=True)

@ray.remote(num_gpus=1)
def use_gpu():
    print("ray.get_gpu_ids(): {}".format(ray.get_gpu_ids()[0]))
    print("CUDA_VISIBLE_DEVICES: {}".format(os.environ["CUDA_VISIBLE_DEVICES"]))

use_gpu.remote()

2020-07-28 11:36:54,049	INFO resource_spec.py:212 -- Starting Ray with 0.98 GiB memory available for workers and up to 1.0 GiB for objects. You can adjust these settings with ray.init(memory=<bytes>, object_store_memory=<bytes>).
2020-07-28 11:36:54,434	INFO services.py:1170 -- View the Ray dashboard at localhost:8266


ObjectID(45b95b1c8bd3a9c4ffffffff010000c801000000)

# Load New and Process Data from website data.brasil.io

In [3]:
import get_data
LoadData=True

if LoadData:
    get_data.get_data()

Baixando arquivos brasil.io...
(pid=34949) ray.get_gpu_ids(): 3
(pid=34949) CUDA_VISIBLE_DEVICES: 3


# Functions to Load Processed Data

In [4]:
def load_confirmed(districtRegion, start_date):
    dateparse = lambda x: datetime.strptime(x, '%Y-%m-%d')
    df = pd.read_csv('./data/DRS_confirmados.csv',delimiter=',',parse_dates=True, date_parser=dateparse)
    y=[]
    x=[]
    for i in range(0,len(df.date)):
        y.append(df[districtRegion].values[i])
        x.append(df.date.values[i])
    df2=pd.DataFrame(data=y,index=x,columns=[""])
    df2=df2[start_date:]
    del x,y,df,dateparse
    return df2

def load_dead(districtRegion, start_date):
    dateparse = lambda x: datetime.strptime(x, '%Y-%m-%d')
    df = pd.read_csv('./data/DRS_mortes.csv',delimiter=',',parse_dates=True, date_parser=dateparse)
    y=[]
    x=[]
    for i in range(0,len(df.date)):
        y.append(df[districtRegion].values[i])
        x.append(df.date.values[i])
    df2=pd.DataFrame(data=y,index=x,columns=[""])
    df2=df2[start_date:]
    del x,y,df,dateparse
    return df2

# Load solver

In [5]:
import LearnerICRayNoLoadBH as L 

# Data for States

In [6]:
dfparam = pd.read_csv("data/param.csv")
dfPopEst = pd.read_csv("data/DRS_popEst.csv")
dfparam['popEst']=dfPopEst.popEst
display(dfparam)

DRS  start-date  prediction-range         s0  \
0        DRS 01 - Grande São Paulo  2020-03-20               200  2000000.0   
1               DRS 02 - Araçatuba  2020-04-01               200      500.0   
2              DRS 03 - Araraquara  2020-04-01               200     2000.0   
3        DRS 04 - Baixada Santista  2020-04-01               200     8000.0   
4                DRS 05 - Barretos  2020-04-01               200     2000.0   
5                   DRS 06 - Bauru  2020-04-01               200    10000.0   
6                DRS 07 - Campinas  2020-04-01               200    20000.0   
7                  DRS 08 - Franca  2020-04-01               200     1000.0   
8                 DRS 09 - Marília  2020-04-01               200     5000.0   
9              DRS 10 - Piracicaba  2020-04-01               200    10000.0   
10    DRS 11 - Presidente Prudente  2020-04-01               200     1000.0   
11               DRS 12 - Registro  2020-04-01               200     1000.0   
12         DRS 13 - Ribeirão Preto  2020-04-01               200     5000.0   
13  DRS 14 - São João da Boa Vista  2020-04-01               200     2000.0   
14  DRS 15 - São José do Rio Preto  2020-04-01               200    10000.0   
15               DRS 16 - Sorocaba  2020-04-01               200     1200.0   
16                DRS 17 - Taubaté  2020-04-01               200    10000.0   

        e0      a0        i0        r0        d0  START  RATIO  WCASES  WREC  \
0   0.0001  0.0001  800.0000  300.0000  400.0000      0   0.15    0.15  0.05   
1   0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
2   0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
3   0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
4   0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
5   0.0001  0.0001    4.0000    0.0001    0.0001      0   0.15    0.40  0.10   
6   0.0001  0.0001   40.0000    0.0001    0.0001      0   0.15    0.40  0.10   
7   0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
8   0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
9   0.0001  0.0001    0.0001    0.0001    1.0000      0   0.15    0.40  0.10   
10  0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
11  0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
12  0.0001  0.0001    0.0001    0.0001    0.0001      5   0.15    0.40  0.10   
13  0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
14  0.0001  0.0001    0.0001    0.0001    0.0001      0   0.15    0.40  0.10   
15  0.0001  0.0001    2.0000    0.0001    0.0001      0   0.15    0.40  0.10   
16  0.0001  0.0001   17.0000    0.0001    2.0000      0   0.15    0.40  0.10   

        popEst  
0   21702084.0  
1     791256.0  
2    1025982.0  
3    1865397.0  
4     440907.0  
5    1800757.0  
6    4671287.0  
7     713458.0  
8    1144665.0  
9    1586546.0  
10    775627.0  
11    284509.0  
12   1523682.0  
13    834872.0  
14   1629470.0  
15   2530829.0  
16   2548463.0

In [7]:
dfSP = pd.read_csv("data/dados_municipios_SP.csv")

# lista DRSs
DRS = list(dfSP["DRS"].unique())
DRS.remove("Indefinido")

dfSP

date state   city place_type  confirmed  deaths  order_for_place  \
0      2020-07-27    SP  TOTAL      state     487654   21676              152   
1      2020-07-26    SP  TOTAL      state     483982   21606              151   
2      2020-07-25    SP  TOTAL      state     479481   21517              150   
3      2020-07-24    SP  TOTAL      state     463218   21206              149   
4      2020-07-23    SP  TOTAL      state     452007   20894              148   
...           ...   ...    ...        ...        ...     ...              ...   
55411  2020-06-23    SP   Óleo       city          1       0                5   
55412  2020-06-22    SP   Óleo       city          1       0                4   
55413  2020-06-21    SP   Óleo       city          1       0                3   
55414  2020-06-20    SP   Óleo       city          1       0                2   
55415  2020-06-19    SP   Óleo       city          1       0                1   

       is_last      popEst  city_ibge_code  confirmed_per_100k_inhabitants  \
0         True  45919049.0            35.0                      1061.98628   
1        False  45919049.0            35.0                      1053.98960   
2        False  45919049.0            35.0                      1044.18757   
3        False  45919049.0            35.0                      1008.77089   
4        False  45919049.0            35.0                       984.35619   
...        ...         ...             ...                             ...   
55411    False      2496.0       3533809.0                        40.06410   
55412    False      2496.0       3533809.0                        40.06410   
55413    False      2496.0       3533809.0                        40.06410   
55414    False      2496.0       3533809.0                        40.06410   
55415    False      2496.0       3533809.0                        40.06410   

       death_rate               DRS  
0          0.0444        Indefinido  
1          0.0446        Indefinido  
2          0.0449        Indefinido  
3          0.0458        Indefinido  
4          0.0462        Indefinido  
...           ...               ...  
55411      0.0000  DRS 09 - Marília  
55412      0.0000  DRS 09 - Marília  
55413      0.0000  DRS 09 - Marília  
55414      0.0000  DRS 09 - Marília  
55415      0.0000  DRS 09 - Marília  

[55416 rows x 13 columns]

# Functions for Optimization

In [8]:
from scipy.integrate import odeint
import sys
import io
import gc

def create_f(districtRegion,e0,a0,r0,date, ratio, predict_range, version):
                
    def fobjective(point):
        
        dead=  load_dead(districtRegion,date)
        data = load_confirmed(districtRegion,date)*(1-ratio)-dead
        cleanRecovered=False
        s0, deltaDate, i0, d0, startNCases, weigthCases, weigthRecov = point
        end_date=datetime.strptime(date, "%Y-%m-%d") + timedelta(days=deltaDate)
        f=L.Learner.remote(districtRegion, end_date.strftime("%Y-%m-%d"), predict_range,\
                           s0, e0, a0, i0, r0, d0, startNCases, ratio, weigthCases, weigthRecov, \
                           cleanRecovered, version, data, dead, savedata=False)
        result = f.train.remote() 
        result = ray.get(result) 

        del end_date,cleanRecovered, data, dead, point,f         

        gc.collect()

        return result
    return fobjective

In [9]:
@ray.remote(memory=50 * 1024 * 1024, max_calls=1)
def opt(districtRegion,s0,i0,e0,a0,r0,d0,wcases,date,startNCases, ratio, predict_range, popEst, version):

    bounds=[(0.1*popEst,0.9*popEst),(-2,2),(0,4000), (0,1000), (0,250),\
              (0.3,0.8),(0.02,0.08)]
    maxiterations=500
    f=create_f(districtRegion,e0,a0,r0,date, ratio, predict_range, version)
    de = DE(f, bounds, maxiters=maxiterations)
    for step in de.geniterator():
        try:
            idx = step.best_idx
            norm_vector = step.population[idx]
            best_params = de.denormalize([norm_vector])
            del norm_vector, idx
        except:
            print("error in function evaluation")
    p=best_params[0]
    del f, bounds, data, dead,best_params
    
    return p

# Main Code

In [10]:
%%javascript
IPython.OutputArea.prototype._should_scroll = function(lines){
    return true;}

<IPython.core.display.Javascript object>

In [11]:
DRS=dfparam.DRS
display(DRS)
allDRS=True
version="106"
gc.enable()

optimal=[]
if allDRS:
    for districtRegion in DRS:
        #remove previous history file
        strFile='./results/history_'+districtRegion+version+'.csv'
        if os.path.isfile(strFile):
            os.remove(strFile)
        query = dfparam.query('DRS == "{}"'.format(districtRegion)).reset_index()
        parameters = np.array(query.iloc[:, 2:])[0]
        date,predict_range,s0,e0,a0,i0,r0,d0,startNCases,ratio,wcases,wrec,popEst = parameters
        optimal.append(opt.remote(districtRegion,s0,i0,e0,a0,r0,d0,wcases,date,startNCases, \
                                  ratio, predict_range, popEst, version))        
else:
    districtRegion = "DRS 01 - Grande São Paulo" #'DRS 08 - Franca' \
    #'DRS 14 - São João da Boa Vista' #'DRS 04 - Baixada Santista' \
    #'DRS 11 - Presidente Prudente' #'DRS 13 - Ribeirão Preto' \
    #'DRS 05 - Barretos' #'DRS 12 - Registro' #'DRS 15 - São José do Rio Preto' \
    #'DRS 10 - Piracicaba'#'DRS 17 - Taubaté'#'DRS 02 - Araçatuba'# \
    #'DRS 03 - Araraquara' #DRS 07 - Campinas'#'DRS 16 - Sorocaba'#'DRS 06 - Bauru' \
    #'DRS 09 - Marília' #"DRS 01 - Grande São Paulo"

    #remove previous history file
    strFile='./results/history_'+districtRegion+version+'.csv'
    if os.path.isfile(strFile):
        os.remove(strFile)
    query = dfparam.query('DRS == "{}"'.format(districtRegion)).reset_index()
    parameters = np.array(query.iloc[:, 2:])[0]
    date,predict_range,s0,e0,a0,i0,r0,d0,startNCases,ratio,wcases,wrec,popEst = parameters
    optimal.append(opt.remote(districtRegion,s0,i0,e0,a0,r0,d0,wcasesdate,startNCases, \
                              ratio, predict_range, popEst, version))        

0          DRS 01 - Grande São Paulo
1                 DRS 02 - Araçatuba
2                DRS 03 - Araraquara
3          DRS 04 - Baixada Santista
4                  DRS 05 - Barretos
5                     DRS 06 - Bauru
6                  DRS 07 - Campinas
7                    DRS 08 - Franca
8                   DRS 09 - Marília
9                DRS 10 - Piracicaba
10      DRS 11 - Presidente Prudente
11                 DRS 12 - Registro
12           DRS 13 - Ribeirão Preto
13    DRS 14 - São João da Boa Vista
14    DRS 15 - São José do Rio Preto
15                 DRS 16 - Sorocaba
16                  DRS 17 - Taubaté
Name: DRS, dtype: object

In [ ]:
optimal=ray.get(optimal)


2020-07-28 11:37:16,294	WARNING worker.py:1090 -- WARNING: 30 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.
2020-07-28 11:37:16,605	WARNING worker.py:1090 -- WARNING: 31 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.
2020-07-28 11:37:16,607	WARNING worker.py:1090 -- WARNING: 32 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.
2020-07-28 11:37:16,618	WARNING worker.py:1090 -- WARNING: 33 PYTHON workers have been started. This could be a 

(pid=35138) basinhopping step 0: f 2.24735e+06
(pid=35132) basinhopping step 0: f 2.1095e+06
(pid=35134) basinhopping step 0: f 7.63143e+07
(pid=35138) basinhopping step 1: f 1.79901e+06 trial_f 1.79901e+06 accepted 1  lowest_f 1.79901e+06
(pid=35138) found new global minimum on step 1 with function value 1.79901e+06
(pid=35239) basinhopping step 0: f 2.8741e+07
(pid=35138) basinhopping step 2: f 1.79901e+06 trial_f 2.16936e+06 accepted 0  lowest_f 1.79901e+06
(pid=35302) basinhopping step 0: f 2.1119e+07
(pid=35298) basinhopping step 0: f 1.25705e+07
(pid=35237) basinhopping step 0: f 2.62757e+06
(pid=35329) basinhopping step 0: f 1.25979e+07
(pid=35133) basinhopping step 0: f 7.93671e+06
(pid=35316) basinhopping step 0: f 2.1341e+06
(pid=35239) basinhopping step 1: f 2.8741e+07 trial_f 5.59091e+11 accepted 0  lowest_f 2.8741e+07
(pid=35239) basinhopping step 2: f 2.8741e+07 trial_f 5.59074e+11 accepted 0  lowest_f 2.8741e+07
(pid=35132) basinhopping step 1: f 2.1095e+06 trial_f 4.513

(pid=35133) basinhopping step 3: f 7.93671e+06 trial_f 4.63899e+08 accepted 0  lowest_f 7.93671e+06
(pid=35139) basinhopping step 2: f 2.17503e+06 trial_f 2.07321e+11 accepted 0  lowest_f 2.17503e+06
(pid=35130) basinhopping step 3: f -1.62575e+09 trial_f 894329 accepted 0  lowest_f -1.62575e+09
(pid=35237) basinhopping step 7: f 659211 trial_f 4.69413e+09 accepted 0  lowest_f 659211
(pid=35133) basinhopping step 4: f 7.93671e+06 trial_f 6.89256e+11 accepted 0  lowest_f 7.93671e+06
(pid=35239) basinhopping step 7: f 2.87408e+07 trial_f 1.3165e+10 accepted 0  lowest_f 2.87408e+07
(pid=35136) /home/ats4i/anaconda3/envs/geo_env/lib/python3.6/site-packages/scipy/integrate/odepack.py:248: ODEintWarning: Excess work done on this call (perhaps wrong Dfun type). Run with full_output = 1 to get quantitative information.
(pid=35136)   warnings.warn(warning_msg, ODEintWarning)
(pid=35239) basinhopping step 8: f 2.87408e+07 trial_f 2.9715e+07 accepted 0  lowest_f 2.87408e+07
(pid=35239) basinhoppi

2020-07-28 11:38:00,144	WARNING worker.py:1090 -- WARNING: 34 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.
2020-07-28 11:38:00,146	WARNING worker.py:1090 -- WARNING: 35 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.


(pid=35535) basinhopping step 0: f 2.78353e+06
(pid=35535) basinhopping step 1: f 2.78353e+06 trial_f 1.72572e+11 accepted 0  lowest_f 2.78353e+06
(pid=35237) basinhopping step 10: f 659211 trial_f 3.08347e+10 accepted 0  lowest_f 659211
(pid=35535) basinhopping step 2: f 1.19979e+06 trial_f 1.19979e+06 accepted 1  lowest_f 1.19979e+06
(pid=35535) found new global minimum on step 2 with function value 1.19979e+06
(pid=35316) basinhopping step 4: f -1.44514e+10 trial_f 1.68925e+09 accepted 0  lowest_f -1.44514e+10
(pid=35535) basinhopping step 3: f 1.19979e+06 trial_f 1.72572e+11 accepted 0  lowest_f 1.19979e+06
(pid=35536) basinhopping step 0: f 1.62332e+06
(pid=35135) basinhopping step 6: f -1.748e+12 trial_f -2.15325e+10 accepted 0  lowest_f -1.748e+12
(pid=35131) basinhopping step 5: f -1.19394e+11 trial_f 347956 accepted 0  lowest_f -1.19394e+11
(pid=35136) basinhopping step 2: f -2.10371e+14 trial_f -2.10371e+14 accepted 1  lowest_f -2.10371e+14
(pid=35136) found new global minimu

...

(pid=131578) basinhopping step 1: f 1.52711e+06 trial_f 1.01321e+09 accepted 0  lowest_f 1.52711e+06
(pid=131382) basinhopping step 9: f 446180 trial_f 1.27676e+10 accepted 0  lowest_f 446180
(pid=131130) basinhopping step 9: f -5.18265e+11 trial_f 2.38414e+07 accepted 0  lowest_f -5.18265e+11
(pid=131656) basinhopping step 0: f 1.41854e+06
(pid=131373) basinhopping step 6: f -1.70838e+11 trial_f 1.74497e+09 accepted 0  lowest_f -1.70838e+11
(pid=131382) warning: basinhopping: local minimization failure
(pid=131382) basinhopping step 10: f 446180 trial_f 1.45523e+08 accepted 0  lowest_f 446180
(pid=131212) basinhopping step 10: f -3.76413e+11 trial_f -8.94814e+10 accepted 0  lowest_f -3.76413e+11
(pid=131656) warning: basinhopping: local minimization failure
(pid=131656) basinhopping step 1: f 1.41362e+06 trial_f 1.41362e+06 accepted 1  lowest_f 1.41362e+06
(pid=131656) found new global minimum on step 1 with function value 1.41362e+06
(pid=131671) basinhopping step 0: f 1.91886e+06
(p

2020-07-28 16:47:31,315	WARNING worker.py:1090 -- WARNING: 34 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.
2020-07-28 16:47:31,317	WARNING worker.py:1090 -- WARNING: 35 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.


(pid=131340) basinhopping step 9: f -7.33341e+09 trial_f 4.04304e+08 accepted 0  lowest_f -7.33341e+09
(pid=131657) basinhopping step 1: f 1.08979e+07 trial_f 1.08979e+07 accepted 1  lowest_f 1.08979e+07
(pid=131657) found new global minimum on step 1 with function value 1.08979e+07
(pid=131471) basinhopping step 0: f -4.80535e+09
(pid=131130) basinhopping step 10: f -5.18265e+11 trial_f 1.02799e+07 accepted 0  lowest_f -5.18265e+11
(pid=131371) basinhopping step 3: f 1.47205e+08 trial_f 1.65961e+09 accepted 0  lowest_f 1.47205e+08
(pid=131838) basinhopping step 0: f 8.27415e+06
(pid=131838) basinhopping step 1: f 8.27415e+06 trial_f 9.46258e+11 accepted 0  lowest_f 8.27415e+06
(pid=131655) basinhopping step 1: f 4.28415e+07 trial_f 4.59928e+07 accepted 0  lowest_f 4.28415e+07
(pid=131471) warning: basinhopping: local minimization failure
(pid=131471) basinhopping step 1: f -4.80535e+09 trial_f 7.40226e+09 accepted 0  lowest_f -4.80535e+09
(pid=131471) basinhopping step 2: f -4.80535e+

2020-07-28 16:47:43,321	WARNING worker.py:1090 -- WARNING: 34 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.
2020-07-28 16:47:43,324	WARNING worker.py:1090 -- WARNING: 35 PYTHON workers have been started. This could be a result of using a large number of actors, or it could be a consequence of using nested tasks (see https://github.com/ray-project/ray/issues/3644) for some a discussion of workarounds.


(pid=131656) basinhopping step 4: f 1.32798e+06 trial_f 1.32798e+06 accepted 1  lowest_f 1.32798e+06
(pid=131656) found new global minimum on step 4 with function value 1.32798e+06
(pid=131656) basinhopping step 5: f 1.32798e+06 trial_f 1.32798e+06 accepted 1  lowest_f 1.32798e+06
(pid=131656) found new global minimum on step 5 with function value 1.32798e+06
(pid=131864) basinhopping step 0: f 1.32116e+06
(pid=131864) basinhopping step 1: f 1.32116e+06 trial_f 1.1684e+11 accepted 0  lowest_f 1.32116e+06
(pid=131369) basinhopping step 9: f -1.11784e+12 trial_f -1.11784e+12 accepted 1  lowest_f -1.11784e+12
(pid=131369) found new global minimum on step 9 with function value -1.11784e+12
(pid=131656) basinhopping step 6: f 1.32798e+06 trial_f 8.92647e+09 accepted 0  lowest_f 1.32798e+06
(pid=131373) basinhopping step 8: f -1.70838e+11 trial_f 1.73673e+09 accepted 0  lowest_f -1.70838e+11
(pid=131837) warning: basinhopping: local minimization failure
(pid=131837) basinhopping step 0: f -2

In [ ]:
for i in range(0,len(DRS)):    

    districtRegion=DRS[i]
    query = dfparam.query('DRS == "{}"'.format(districtRegion)).reset_index()
    parameters = np.array(query.iloc[:, 2:])[0]
    startdate,predict_range,s0,e0,a0,i0,r0,d0,startNCases,ratio,wcases,wrec = parameters
    Date = datetime.strptime(startdate, "%Y-%m-%d")
    end_date = Date + timedelta(days=+int(optimal[i][1]))
    dateStr=end_date.strftime("%Y-%m-%d")

    j = query['index'].values[0]
    dfparam.at[j, "s0"] = optimal[i][0]
    dfparam.at[j, "start-date"] = dateStr
    dfparam.at[j, "i0"] = optimal[i][2]
    dfparam.at[j, "WCASES"] = optimal[i][3]
    dfparam.at[j, "WREC"] = optimal[i][4]

    dfparam.to_csv("data/param_optimized_Yabox.csv", sep=",", index=False)
    dfparam
    